# Farina in Natura - estratégia

![](Logo_farina_in_natura_edited.jpg)

## Importando os dados e observações iniciais

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns; sns.set()
import datetime
import nbformat
import chart_studio
import plotly.express as px
import cufflinks as cf

from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode (connected = True )
cf.go_offline()
# chart_studio.tools.set_credentials_file(username='claudio.oliveira', api_key='fXrLqCmkdJQyTheCzYMS')
from IPython.display import display


In [2]:
from fpdf import FPDF

In [3]:
from IPython.display import display
pd.options.display.max_columns = None
pd.options.display.max_rows = None

In [4]:
# para resolver o problema: "(unicode error) 'utf-8' codec can't decode "
# https://www.youtube.com/watch?v=ZSC7X4N8RKo,
#Erro: 
# UnicodeDecodeError: 'utf-8' codec can't decode byte 0xe9 in position 900: invalid continuation byte
# enem = pd.read_csv("MICRODADOS_ENEM_2020.csv", encoding="utf-8", sep = ';')
# enem = pd.read_csv("MICRODADOS_ENEM_2020.csv", encoding="ISO-8859-1", sep = ';')

transactions = pd.read_csv(r'C:\Users\ctobr\OneDrive\DATA_Science\1_farina_in_natura\farina_in_natura00\CSV\farina.CSV', 
encoding="ISO-8859-1", sep = ';')

In [5]:
transactions.head()

venda         data_hora     cliente mesa   item                produto  \
0  460.0  01/02/2022 08:13  CONSUMIDOR  M 1  119.0  SUCO DE LARANJA 400ML   
1  460.0  01/02/2022 08:13  CONSUMIDOR  M 1  121.0     PAO SOURDOUGH OVOS   
2  461.0  01/02/2022 08:14  CONSUMIDOR  M 2  119.0  SUCO DE LARANJA 400ML   
3  461.0  01/02/2022 08:14  CONSUMIDOR  M 2  121.0     PAO SOURDOUGH OVOS   
4  465.0  01/02/2022 09:01  CONSUMIDOR  M 1   46.0       QUICHE BACON 90G   

   quantidade valor_unit  desconto total_item  
0         1.0       14,5       0.0       14,5  
1         1.0       15,5       0.0       15,5  
2         1.0       14,5       0.0       14,5  
3         1.0       15,5       0.0       15,5  
4         2.0       19,5       0.0         39

In [6]:
transactions.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 25998 entries, 0 to 25997
Data columns (total 10 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   venda       25992 non-null  float64
 1   data_hora   25992 non-null  object 
 2   cliente     25992 non-null  object 
 3   mesa        22779 non-null  object 
 4   item        25922 non-null  float64
 5   produto     25992 non-null  object 
 6   quantidade  25992 non-null  float64
 7   valor_unit  25992 non-null  object 
 8   desconto    25992 non-null  float64
 9   total_item  25992 non-null  object 
dtypes: float64(4), object(6)
memory usage: 2.0+ MB


# Limpeza e manipulação dos dados

In [7]:
### CHECK OUT IF THE NUMBER OF TOTAL ENTRIES IS EQUAL TO THE NUMBER OF ENTRIES OF THE VARIABLES  

transactions.isnull().sum()

venda            6
data_hora        6
cliente          6
mesa          3219
item            76
produto          6
quantidade       6
valor_unit       6
desconto         6
total_item       6
dtype: int64

In [8]:
## DROPPING THE ROWS THAT ALL COLUMN VALUES ARE NULL
#  https://www.youtube.com/watch?v=uDr67HBIPz8&t=818s

transactions = transactions.dropna(how='all')

In [9]:
# Delete the column "item"

del transactions["item"]

In [10]:
transactions.info()
transactions.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 25992 entries, 0 to 25997
Data columns (total 9 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   venda       25992 non-null  float64
 1   data_hora   25992 non-null  object 
 2   cliente     25992 non-null  object 
 3   mesa        22779 non-null  object 
 4   produto     25992 non-null  object 
 5   quantidade  25992 non-null  float64
 6   valor_unit  25992 non-null  object 
 7   desconto    25992 non-null  float64
 8   total_item  25992 non-null  object 
dtypes: float64(3), object(6)
memory usage: 2.0+ MB


venda         data_hora     cliente mesa                produto  \
0  460.0  01/02/2022 08:13  CONSUMIDOR  M 1  SUCO DE LARANJA 400ML   
1  460.0  01/02/2022 08:13  CONSUMIDOR  M 1     PAO SOURDOUGH OVOS   
2  461.0  01/02/2022 08:14  CONSUMIDOR  M 2  SUCO DE LARANJA 400ML   
3  461.0  01/02/2022 08:14  CONSUMIDOR  M 2     PAO SOURDOUGH OVOS   
4  465.0  01/02/2022 09:01  CONSUMIDOR  M 1       QUICHE BACON 90G   

   quantidade valor_unit  desconto total_item  
0         1.0       14,5       0.0       14,5  
1         1.0       15,5       0.0       15,5  
2         1.0       14,5       0.0       14,5  
3         1.0       15,5       0.0       15,5  
4         2.0       19,5       0.0         39

In [11]:
## Using isna() to select all rows with NaN in the column ('mesa') and the value "CONSUMIDOR" on the column "cliente" 
## and replace the "mesa" value with "M0"
## https://datatofish.com/rows-with-nan-pandas-dataframe/
## https://www.geeksforgeeks.org/how-to-replace-values-in-column-based-on-condition-in-pandas/

transactions.loc[(transactions["cliente"] == 'CONSUMIDOR') &  (transactions['mesa'].isna()), 'mesa']= 'M0'


In [12]:
# Checking if the changes were correct.

transactions.loc[transactions["mesa"] == 'M0']

venda         data_hora     cliente mesa                      produto  \
121  520.0  02/02/2022 16:57  CONSUMIDOR   M0        BOMBOLONI NUTELLA 80G   
122  520.0  02/02/2022 16:57  CONSUMIDOR   M0    TARTELETE DE MORANGO 120G   
123  520.0  02/02/2022 16:57  CONSUMIDOR   M0      CROISSANT MUSSATRELA DE   
894  856.0  11/02/2022 19:19  CONSUMIDOR   M0  CROISSANT BRIE PARMA MEL DE   
895  856.0  11/02/2022 19:19  CONSUMIDOR   M0    VH SANTA HORTENSIA SAUVIG   

     quantidade valor_unit  desconto total_item  
121         2.0         12       0.0         24  
122         1.0         18       0.0         18  
123         1.0       25,5       0.0       25,5  
894         2.0       25,5       0.0         51  
895         1.0         59       0.0         59

In [13]:
# Assigning a value "ND" to the empty records in column "mesa"
# https://www.w3schools.com/python/pandas/pandas_cleaning_empty_cells.asp

transactions['mesa'].fillna("ND",inplace = True )

In [14]:
# Convert the "venda" variable from float64 type to integer type
# https://stackoverflow.com/questions/43956335/convert-float64-column-to-int64-in-pandas

transactions['venda'] = np.int64(transactions['venda'])

In [15]:
# Convert the "quantidade" variable from float64 type to integer type
# https://stackoverflow.com/questions/43956335/convert-float64-column-to-int64-in-pandas

transactions['quantidade'] = np.int64(transactions['quantidade'])

In [16]:
# change the decimal delimiter of the the variable "valor_unit" from "," to "."
# https://cursos.alura.com.br/forum/topico-transformar-pontos-por-virgulas-dentro-de-um-dataframe-121090
transactions['valor_unit'] = transactions['valor_unit'].str.replace(",",".")

# Convert the "valor_uni" variable from object type to float64 type
# https://www.statology.org/pandas-convert-object-to-float/

transactions['valor_unit'] = transactions['valor_unit'].astype(float)

In [17]:
# change the decimal delimiter of the the variable "total_item" from "," to "."
# https://cursos.alura.com.br/forum/topico-transformar-pontos-por-virgulas-dentro-de-um-dataframe-121090
transactions['total_item'] = transactions['total_item'].str.replace(",",".")

# Convert the "total_item" variable from object type to float64 type
# https://www.statology.org/pandas-convert-object-to-float/

transactions['total_item'] = transactions['total_item'].astype(float)

In [18]:


# Convert "data_hora" to datetime object
transactions['data_hora'] = pd.to_datetime(transactions['data_hora'], format='%d/%m/%Y %H:%M')

# Creating a horario column that is a copy of data_hora and coverting it to datetime and extracting only the day;
transactions['horario'] = (transactions['data_hora'])
transactions['horario'] = transactions['horario'].dt.date

#How to Solve Python ValueError: unconverted data remains
#read://https_researchdatapod.com/?url=https%3A%2F%2Fresearchdatapod.com%2Fhow-to-solve-python-valueerror-unconverted-data-remains%2F

In [19]:
transactions.head()

venda           data_hora     cliente mesa                produto  \
0    460 2022-02-01 08:13:00  CONSUMIDOR  M 1  SUCO DE LARANJA 400ML   
1    460 2022-02-01 08:13:00  CONSUMIDOR  M 1     PAO SOURDOUGH OVOS   
2    461 2022-02-01 08:14:00  CONSUMIDOR  M 2  SUCO DE LARANJA 400ML   
3    461 2022-02-01 08:14:00  CONSUMIDOR  M 2     PAO SOURDOUGH OVOS   
4    465 2022-02-01 09:01:00  CONSUMIDOR  M 1       QUICHE BACON 90G   

   quantidade  valor_unit  desconto  total_item     horario  
0           1        14.5       0.0        14.5  2022-02-01  
1           1        15.5       0.0        15.5  2022-02-01  
2           1        14.5       0.0        14.5  2022-02-01  
3           1        15.5       0.0        15.5  2022-02-01  
4           2        19.5       0.0        39.0  2022-02-01

In [20]:
transactions.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 25992 entries, 0 to 25997
Data columns (total 10 columns):
 #   Column      Non-Null Count  Dtype         
---  ------      --------------  -----         
 0   venda       25992 non-null  int64         
 1   data_hora   25992 non-null  datetime64[ns]
 2   cliente     25992 non-null  object        
 3   mesa        25992 non-null  object        
 4   produto     25992 non-null  object        
 5   quantidade  25992 non-null  int64         
 6   valor_unit  25992 non-null  float64       
 7   desconto    25992 non-null  float64       
 8   total_item  25992 non-null  float64       
 9   horario     25992 non-null  object        
dtypes: datetime64[ns](1), float64(3), int64(2), object(4)
memory usage: 2.2+ MB


In [21]:

# https://www.dataquest.io/blog/python-datetime-tutorial/


#  add hora and minuto column; using class attributes .hour and .minute

transactions['hora'] = transactions.data_hora.dt.hour
transactions['minuto'] = transactions.data_hora.dt.minute



### Renaming the column "data_hora" to "data"

In [22]:
# https://www.statology.org/pandas-rename-columns/
# renaming the column

transactions.rename(columns = {'data_hora':'data'}, inplace = True)


### Extracting only the Date from 'data' column

In [23]:

## https://datagy.io/pandas-extract-date-from-datetime/
transactions['data'] = transactions['data'].dt.normalize()

In [24]:
# Definindo a função time_of_day
def time_of_day(hora):
    """
    Determina se a  compra foi feita pela manhã, tarde ou noite.
    """
    
    if hora < 12:
        
        return 'manhã'
    
    elif hora < 17:
        
        return 'tarde'
    
    else:
        
        return 'noite'

In [25]:
# Apply time of day function to 'hora' column

transactions['time_of_day'] = transactions.hora.apply(time_of_day)


In [26]:
# https://pt.stackoverflow.com/questions/508484/mostrar-dias-da-semana#:~:text=Como%20weekday()%20retorna%20um,fim%20de%20semana%20ou%20n%C3%A3o.

import locale
# setar locale para português para que os dias da semana retornem em portugês no código abaixo.
locale.setlocale(locale.LC_ALL, 'pt_BR.utf8')

'pt_BR.utf8'

In [166]:
# Add a day of week variable and a second classifier of weekday or weekend

from datetime import date
import calendar

transactions['day_of_week'] = [calendar.day_name[i.weekday()] for i in transactions['horario']]


In [29]:
transactions.head()

venda       data     cliente mesa                produto  quantidade  \
0    460 2022-02-01  CONSUMIDOR  M 1  SUCO DE LARANJA 400ML           1   
1    460 2022-02-01  CONSUMIDOR  M 1     PAO SOURDOUGH OVOS           1   
2    461 2022-02-01  CONSUMIDOR  M 2  SUCO DE LARANJA 400ML           1   
3    461 2022-02-01  CONSUMIDOR  M 2     PAO SOURDOUGH OVOS           1   
4    465 2022-02-01  CONSUMIDOR  M 1       QUICHE BACON 90G           2   

   valor_unit  desconto  total_item     horario  hora  minuto time_of_day  \
0        14.5       0.0        14.5  2022-02-01     8      13       manhã   
1        15.5       0.0        15.5  2022-02-01     8      13       manhã   
2        14.5       0.0        14.5  2022-02-01     8      14       manhã   
3        15.5       0.0        15.5  2022-02-01     8      14       manhã   
4        19.5       0.0        39.0  2022-02-01     9       1       manhã   

   day_of_week  
0  terça-feira  
1  terça-feira  
2  terça-feira  
3  terça-feira  
4  terça-feira

In [173]:

transactions['day_type'] = ['FDS' if (i == 'domingo') | (i == 'sábado') else 'DDS' for i in 
                                                                            transactions['day_of_week']]


In [31]:
transactions.rename(columns = {'day_of_week':'dia_da_semana'}, inplace = True)

In [32]:
transactions.rename(columns = {'time_of_day':'hora_do_dia'}, inplace = True)

In [33]:
transactions.rename(columns = {'day_type':'tipo_de_dia'}, inplace = True)

In [34]:
# Add an item count variable equal to one for future groupby operations

transactions['item_count'] = 1


In [168]:
transactions.head()

venda       data     cliente mesa                produto  quantidade  \
0    460 2022-02-01  CONSUMIDOR  M 1  SUCO DE LARANJA 400ML           1   
1    460 2022-02-01  CONSUMIDOR  M 1     PAO SOURDOUGH OVOS           1   
2    461 2022-02-01  CONSUMIDOR  M 2  SUCO DE LARANJA 400ML           1   
3    461 2022-02-01  CONSUMIDOR  M 2     PAO SOURDOUGH OVOS           1   
4    465 2022-02-01  CONSUMIDOR  M 1       QUICHE BACON 90G           2   

   valor_unit  desconto  total_item     horario  hora  minuto hora_do_dia  \
0        14.5       0.0        14.5  2022-02-01     8      13       manhã   
1        15.5       0.0        15.5  2022-02-01     8      13       manhã   
2        14.5       0.0        14.5  2022-02-01     8      14       manhã   
3        15.5       0.0        15.5  2022-02-01     8      14       manhã   
4        19.5       0.0        39.0  2022-02-01     9       1       manhã   

  dia_da_semana tipo_de_dia  item_count  day_of_week day_type  
0   terça-feira         DDS           1  terça-feira      DDS  
1   terça-feira         DDS           1  terça-feira      DDS  
2   terça-feira         DDS           1  terça-feira      DDS  
3   terça-feira         DDS           1  terça-feira      DDS  
4   terça-feira         DDS           1  terça-feira      DDS

In [36]:
transactions.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 25992 entries, 0 to 25997
Data columns (total 16 columns):
 #   Column         Non-Null Count  Dtype         
---  ------         --------------  -----         
 0   venda          25992 non-null  int64         
 1   data           25992 non-null  datetime64[ns]
 2   cliente        25992 non-null  object        
 3   mesa           25992 non-null  object        
 4   produto        25992 non-null  object        
 5   quantidade     25992 non-null  int64         
 6   valor_unit     25992 non-null  float64       
 7   desconto       25992 non-null  float64       
 8   total_item     25992 non-null  float64       
 9   horario        25992 non-null  object        
 10  hora           25992 non-null  int64         
 11  minuto         25992 non-null  int64         
 12  hora_do_dia    25992 non-null  object        
 13  dia_da_semana  25992 non-null  object        
 14  tipo_de_dia    25992 non-null  object        
 15  item_count     2599

# Verificando alguma divergência dos dados

In [37]:
# Verificando se o valor "total_item" é igual a: "quantidade" * "valor_unit"

transactions["total_item_verif"] = transactions['quantidade']* transactions['valor_unit']

In [38]:
# Continuando o item anterior
# https://www.dataquest.io/blog/tutorial-add-column-pandas-dataframe-based-on-if-else-condition/

transactions['confirm'] = np.where(transactions['total_item'] > transactions['total_item_verif'], True, False)


In [39]:
# continuando o item anterior
resumo = transactions.loc[transactions["confirm"] == True].sum()
print (resumo)

venda                                                        13730391
cliente             CONSUMIDORCONSUMIDORCONSUMIDORCONSUMIDORIFOODC...
mesa                M 5M 13M 11M 5NDM 19NDM 13M 13M 17NDM 23M 23M ...
produto             CROISSANTCROISSANTCROISSANTCROISSANTCROISSANT ...
quantidade                                                       2139
valor_unit                                                    21083.7
desconto                                                          0.0
total_item                                                    53878.3
hora                                                            29332
minuto                                                          59296
hora_do_dia         manhãmanhãtardemanhãmanhãmanhãmanhãnoitenoiten...
dia_da_semana       sexta-feirasexta-feirasexta-feirasábadosábados...
tipo_de_dia         DDSDDSDDSDDSDDSDDSDDSDDSDDSDDSDDSDDSDDSDDSDDSD...
item_count                                                       2032
total_item_verif    

C:\Users\ctobr\AppData\Local\Temp\ipykernel_15160\2200306820.py:2: FutureWarning:

The default value of numeric_only in DataFrame.sum is deprecated. In a future version, it will default to False. In addition, specifying 'numeric_only=None' is deprecated. Select only valid columns or specify the value of numeric_only to silence this warning.



In [40]:
# Gerando um relatório em pdf dos dados divergentes
# How do I select specific rows and columns from a DataFrame?
# https://pandas.pydata.org/docs/getting_started/intro_tutorials/03_subset_data.html#how-do-i-select-specific-rows-and-columns-from-a-dataframe
# https://www.geeksforgeeks.org/select-rows-columns-by-name-or-index-in-pandas-dataframe-using-loc-iloc/

ts2 = transactions.loc[transactions["confirm"] == True, ["venda", "produto", "quantidade", "valor_unit", "total_item", "total_item_verif"]]

In [41]:
# Exporting to a pdf file the transactions that has a inconsistent data.
from matplotlib.backends.backend_pdf import PdfPages


In [42]:
# https://levelup.gitconnected.com/how-to-write-a-pandas-dataframe-as-a-pdf-5cdf7d525488

def _draw_as_table(df, pagesize):
    alternating_colors = [['white'] * len(df.columns), ['lightgray'] * len(df.columns)] * len(df)
    alternating_colors = alternating_colors[:len(df)]
    fig, ax = plt.subplots(figsize=pagesize)
    ax.axis("tight")
    ax.axis('off')
    the_table = ax.table(cellText=df.values,
                        rowLabels=df.index,
                        colLabels=df.columns,
                        rowColours=['lightblue']*len(df),
                        colColours=['lightblue']*len(df.columns),
                        cellColours=alternating_colors,
                        loc='center')
    return fig


In [43]:
# https://www.alixaprodev.com/2022/05/convert-pandas-dataframe-to-pdf-in-python.html
#fig, ax =plt.subplots(figsize=(14,6))
#ax.axis('equal')
#ax.axis('off')
#the_table = ax.table(cellText=ts2.values,colLabels=ts2.columns,loc='center')




In [44]:
def dataframe_to_pdf(df, filename, numpages=(1, 1), pagesize=(11, 8.5)):
  with PdfPages(filename) as pdf:
    nh, nv = numpages
    rows_per_page = len(df) // nh
    cols_per_page = len(df.columns) // nv
    for i in range(0, nh):
        for j in range(0, nv):
            page = df.iloc[(i*rows_per_page):min((i+1)*rows_per_page, len(df)),
                           (j*cols_per_page):min((j+1)*cols_per_page, len(df.columns))]
            fig = _draw_as_table(page, pagesize)
            if nh > 1 or nv > 1:
                # Add a part/page number at bottom-center of page
                fig.text(0.5, 0.5/pagesize[0],
                         "Part-{}x{}: Page-{}".format(i+1, j+1, i*nv + j + 1),
                         ha='center', fontsize=8)
            pdf.savefig(fig, bbox_inches='tight')
            
            plt.close()

In [45]:
### Trying to Align the page number
# https://www.geeksforgeeks.org/matplotlib-figure-figure-text-in-python/
def dataframe_to_pdf(df, filename, numpages=(1, 1), pagesize=(11, 8.5)):
  with PdfPages(filename) as pdf:
    nh, nv = numpages
    rows_per_page = len(df) // nh
    cols_per_page = len(df.columns) // nv
    for i in range(0, nh):
        for j in range(0, nv):
            page = df.iloc[(i*rows_per_page):min((i+1)*rows_per_page, len(df)),
                           (j*cols_per_page):min((j+1)*cols_per_page, len(df.columns))]
            fig = _draw_as_table(page, pagesize)
            #if nh > 1 or nv > 1:
                # Add a part/page number at bottom-center of page
                #fig.text(0.5, 0.5/pagesize[0],
                       # "Part-{}x{}: Page-{}".format(i+1, j+1, i*nv + j + 1),
                       # verticalalignment ='bottom', 
                       # horizontalalignment ='right',
                       #transform = ax.transAxes,
                        #color ='green',
                        #fontsize = 5
                         #)
            pdf.savefig(fig, bbox_inches='tight')
            
            plt.close()

### Creating a pdf file from the divergent data

In [46]:
# dataframe_to_pdf(ts2, "diverge_01.pdf", numpages=(12, 1), pagesize=(11.7, 8.3))

In [47]:
## Create a HTML file of the resumé "ts2" dataframe.

f = open('exp.html','w')
a = ts2.to_html()
f.write(a)
f.close()

In [48]:
# drop the 'confirm" and "total_item_verif" column
transactions = transactions.drop(['confirm'], axis=1)
transactions = transactions.drop(['total_item_verif'], axis=1)


In [49]:
transactions.head()

venda       data     cliente mesa                produto  quantidade  \
0    460 2022-02-01  CONSUMIDOR  M 1  SUCO DE LARANJA 400ML           1   
1    460 2022-02-01  CONSUMIDOR  M 1     PAO SOURDOUGH OVOS           1   
2    461 2022-02-01  CONSUMIDOR  M 2  SUCO DE LARANJA 400ML           1   
3    461 2022-02-01  CONSUMIDOR  M 2     PAO SOURDOUGH OVOS           1   
4    465 2022-02-01  CONSUMIDOR  M 1       QUICHE BACON 90G           2   

   valor_unit  desconto  total_item     horario  hora  minuto hora_do_dia  \
0        14.5       0.0        14.5  2022-02-01     8      13       manhã   
1        15.5       0.0        15.5  2022-02-01     8      13       manhã   
2        14.5       0.0        14.5  2022-02-01     8      14       manhã   
3        15.5       0.0        15.5  2022-02-01     8      14       manhã   
4        19.5       0.0        39.0  2022-02-01     9       1       manhã   

  dia_da_semana tipo_de_dia  item_count  
0   terça-feira         DDS           1  
1   terça-feira         DDS           1  
2   terça-feira         DDS           1  
3   terça-feira         DDS           1  
4   terça-feira         DDS           1

In [50]:
transactions.info()


<class 'pandas.core.frame.DataFrame'>
Int64Index: 25992 entries, 0 to 25997
Data columns (total 16 columns):
 #   Column         Non-Null Count  Dtype         
---  ------         --------------  -----         
 0   venda          25992 non-null  int64         
 1   data           25992 non-null  datetime64[ns]
 2   cliente        25992 non-null  object        
 3   mesa           25992 non-null  object        
 4   produto        25992 non-null  object        
 5   quantidade     25992 non-null  int64         
 6   valor_unit     25992 non-null  float64       
 7   desconto       25992 non-null  float64       
 8   total_item     25992 non-null  float64       
 9   horario        25992 non-null  object        
 10  hora           25992 non-null  int64         
 11  minuto         25992 non-null  int64         
 12  hora_do_dia    25992 non-null  object        
 13  dia_da_semana  25992 non-null  object        
 14  tipo_de_dia    25992 non-null  object        
 15  item_count     2599

> # **Exploração dos Dados**

In [ ]:
# Find Unique Values of each item sold in the Column "produto"
# https://www.statology.org/pandas-unique-values-in-column/
transactions.produto.value_counts()

In [ ]:
# find the percentage each item is selling
transactions.produto.value_counts(True)

In [53]:
## Get unique names in the "produto" column using Series.unique() 
## https://sparkbyexamples.com/pandas/pandas-count-unique-values-in-column/
num_itens_vend = transactions.produto.unique().size

print('O número de diferentes itens vendido pela loja é:', num_itens_vend)

O número de diferentes itens vendido pela loja é: 212


In [54]:
# Look at the average number of items purchased...

avg_items = transactions.groupby(by='venda')['produto'].count().mean()

print('A média de itens por venda é: %.2f itens' %avg_items)

A média de itens por venda é: 2.79 itens


In [55]:
# ...and how that varies by time of day

single_transaction = pd.DataFrame(transactions.groupby(by='venda')['item_count'].sum())

single_transaction = single_transaction.merge(transactions[['hora','minuto','hora_do_dia','data', 'venda']]\
                                              .drop_duplicates('venda'), left_on=single_transaction.index, 
                                              right_on='venda', how='left', copy=False)

print('O número médio de itens vendidos por hora do dia é: \n{0}'.format(
    single_transaction.groupby(by='hora_do_dia')['item_count'].mean()))

O número médio de itens vendidos por hora do dia é: 
hora_do_dia
manhã    3.046419
noite    2.663510
tarde    2.783376
Name: item_count, dtype: float64


In [56]:
# Find the frequency of each item purchased and by time of day

item_frequencies_all = transactions.produto.value_counts()
item_frequencies_morning = transactions[transactions.hora_do_dia == 'manhã'].produto.value_counts()
item_frequencies_afternoon = transactions[transactions.hora_do_dia == 'tarde'].produto.value_counts()
item_frequencies_evening = transactions[transactions.hora_do_dia == 'noite'].produto.value_counts()

In [57]:
# Plot the frequency of purchase for each item

# https://community.plotly.com/t/errors-accessing-plotly-api/33271
# ok, so I found a solution to my problem - when I let my program run through, the error message produced is:
#chart_studio.exceptions.PlotlyRequestError: Authentication credentials were not provided.
#I Googled this error and there were suggestions to run plotly in offline mode by replacing:
#import chart_studio.plotly as py
#with

import plotly.offline as py
#then use py.plot instead of py.iplot

# Solving the problem of the 'plotly' online library with chart_studio
# https://plotly.com/python/getting-started-with-chart-studio/
import plotly.graph_objs as go
#import chart_studio.plotly as py
# import plotly.express as px

button_layer_1_height = 1.12
button_layer_2_height = 1.065

item_threshold_all = 100
item_threshold_other = 50

trace_all = go.Bar(
            x=item_frequencies_all[item_frequencies_all > item_threshold_all].index,
            y=item_frequencies_all[item_frequencies_all > item_threshold_all].values,
            visible=True,
            name='Todo dia'
    )

trace_morning = go.Bar(
            x=item_frequencies_morning[item_frequencies_morning > item_threshold_other].index,
            y=item_frequencies_morning[item_frequencies_morning > item_threshold_other].values,
            visible=False,
            name='Manhã'
    )

trace_afternoon = go.Bar(
            x=item_frequencies_afternoon[item_frequencies_afternoon > item_threshold_other].index,
            y=item_frequencies_afternoon[item_frequencies_afternoon > item_threshold_other].values,
            visible=False,
            name='Tarde'
    )

trace_evening = go.Bar(
            x=item_frequencies_evening[item_frequencies_evening > 10].index,
            y=item_frequencies_evening[item_frequencies_evening > 10].values,
            visible=False,
            name='Noite'
    )

data = [trace_all, trace_morning, trace_afternoon, trace_evening]

updatemenus = list([
    
    dict(
         buttons=list([   
            dict(label = 'Todo dia',
                 method = 'update',
                 args = [{'visible': [True, False, False, False]},
                         {'title': 'Todo Dia'}]),
             
            dict(label = 'Manhã',
                 method = 'update',
                 args = [{'visible': [False, True, False, False]},
                         {'title': 'Manhã'}]),
             
            dict(label = 'Tarde',
                 method = 'update',
                 args = [{'visible': [False, False, True, False]},
                         {'title': 'Tarde'}]),
             
            dict(label = 'Noite',
                 method = 'update',
                 args = [{'visible': [False, False, False, True]},
                         {'title': 'Noite'}])
        ]),
        type='buttons',
        direction = 'right',
        pad = {'r': 10, 't': 10},
        showactive = True,
        x = 0.3,
        xanchor = 'left',
        y = button_layer_1_height,
        yanchor = 'top' )
])
                
layout = dict(title='Vendas Farina por hora do dia', showlegend=False,
              updatemenus=updatemenus)




fig = dict(data=data, layout=layout)
py.plot(fig, filename='frequencies-bar.html')

'frequencies-bar.html'

# Creating an animated frequencie line 

In [ ]:
# Sales trend by date
# https://www.youtube.com/watch?v=Xjm7fOw6gjY
# use reset index for transforming the data in a variable not a index

grouped_by_date = pd.DataFrame(transactions.groupby(by='horario')['item_count'].sum().reset_index())

In [59]:
from chart_studio.grid_objs import Grid, Column
import plotly.figure_factory as ff

# Create a plot.ly-friendly table for Sales per day

table = ff.create_table(grouped_by_date)
py.plot(table, filename='Vendas_por_dia_farina.html')



'Vendas_por_dia_farina.html'

In [60]:
vendas = px.line(grouped_by_date, x = 'horario', y = 'item_count', title = 'Itens vendidos por dia', labels= {'item_count' : 'Quantidade de itens vendidos','data': 'Data'})
py.plot(vendas, filename='Vendas_line_chart.html')

'Vendas_line_chart.html'

In [192]:
grouped_by_date


horario  item_count
0    2022-02-01          74
1    2022-02-02          88
2    2022-02-03          81
3    2022-02-04         110
4    2022-02-05         112
5    2022-02-06         121
6    2022-02-07          61
7    2022-02-09         101
8    2022-02-10          88
9    2022-02-11          87
10   2022-02-12         108
11   2022-02-13         186
12   2022-02-14          77
13   2022-02-16          93
14   2022-02-17          68
15   2022-02-18         106
16   2022-02-19         107
17   2022-02-20         156
18   2022-02-21          75
19   2022-02-23          81
20   2022-02-24          60
21   2022-02-25         106
22   2022-02-26          96
23   2022-02-27          86
24   2022-02-28          91
25   2022-03-01          87
26   2022-03-02          92
27   2022-03-03          73
28   2022-03-04          60
29   2022-03-05         176
30   2022-03-06         126
31   2022-03-07          38
32   2022-03-08          77
33   2022-03-09          51
34   2022-03-10          73
35   2022-03-11          37
36   2022-03-12         135
37   2022-03-13         145
38   2022-03-14          39
39   2022-03-15          67
40   2022-03-16          95
41   2022-03-17         114
42   2022-03-18          48
43   2022-03-19         164
44   2022-03-20         140
45   2022-03-21          72
46   2022-03-22          83
47   2022-03-23          70
48   2022-03-24          67
49   2022-03-25          48
50   2022-03-26         102
51   2022-03-27         121
52   2022-03-28          61
53   2022-03-29          43
54   2022-03-30          65
55   2022-03-31         111
56   2022-04-01          65
57   2022-04-02          65
58   2022-04-03          93
59   2022-04-04          51
60   2022-04-05          56
61   2022-04-06          49
62   2022-04-07          79
63   2022-04-08          89
64   2022-04-09          78
65   2022-04-10          77
66   2022-04-11          40
67   2022-04-12          35
68   2022-04-13         102
69   2022-04-14         104
70   2022-04-15          19
71   2022-04-16          81
72   2022-04-17          97
73   2022-04-18          38
74   2022-04-19          40
75   2022-04-20          52
76   2022-04-21         114
77   2022-04-22          74
78   2022-04-23         126
79   2022-04-24          88
80   2022-04-25          64
81   2022-04-26          54
82   2022-04-27          57
83   2022-04-28          41
84   2022-04-29          42
85   2022-04-30          84
86   2022-05-01         110
87   2022-05-02          59
88   2022-05-03          39
89   2022-05-04          62
90   2022-05-05          65
91   2022-05-06          79
92   2022-05-07         105
93   2022-05-08         123
94   2022-05-09          73
95   2022-05-10          91
96   2022-05-11          96
97   2022-05-12         116
98   2022-05-13         169
99   2022-05-14         227
100  2022-05-15         215
101  2022-05-16         119
102  2022-05-17         106
103  2022-05-18         241
104  2022-05-19         108
105  2022-05-20         141
106  2022-05-21         226
107  2022-05-22         175
108  2022-05-23          97
109  2022-05-24         136
110  2022-05-25          61
111  2022-05-26         136
112  2022-05-27         141
113  2022-05-28         169
114  2022-05-29         154
115  2022-05-30          61
116  2022-05-31          52
117  2022-06-01          40
118  2022-06-02          30
119  2022-06-03          51
120  2022-06-04          84
121  2022-06-05         150
122  2022-06-06          64
123  2022-06-07          45
124  2022-06-08          35
125  2022-06-09          58
126  2022-06-10          50
127  2022-06-11          81
128  2022-06-12         123
129  2022-06-13          48
130  2022-06-14          61
131  2022-06-15          67
132  2022-06-16          71
133  2022-06-17          38
134  2022-06-18          71
135  2022-06-19         114
136  2022-06-20          32
137  2022-06-21          56
138  2022-06-22          32
139  2022-06-23        2303
140  2022-06-24          58
141  2022-06-25         121
142 

In [188]:
# ajustando o gráfio para retirar dois outliers (490 em 2022-07-30 , 2303 em 2022-06-23 ), utilizando-se de filtro com a função 'where'
indice_atip = np.where((grouped_by_date['item_count'] < 400))
linha=grouped_by_date.loc[indice_atip]

In [191]:
# https://towardsdatascience.com/line-chart-animation-with-plotly-on-jupyter-e19c738dc882



#linha=grouped_by_date: usar se precisar demonstrar os dois outliers

trace1 = go.Scatter(x=linha['horario'][:2],
                    y=linha['item_count'][:2],
                    mode='lines',
                    line=dict(width=1.5))

frames = [dict(data= [dict(type='scatter',
                           x=linha['horario'][:k+1],
                           y=linha['item_count'][:k+1]),
                     ],
               traces= [0],  
              )for k  in  range(1, len(linha)-1)]
layout = go.Layout(width=1180,
                   height=750,
                   showlegend=False,
                   hovermode='closest',
                   updatemenus=[
                        dict(
                            type='buttons', showactive=False,
                            y=1.06,
                            x=0.12,
                            xanchor='center',
                            yanchor='auto',
                            pad=dict(t=0, r=10),
                            buttons=[dict(label='Play',
                            method='animate',
                            args=[None, 
                                  dict(frame=dict(duration=90, 
                                                  redraw=False),
                                                  transition=dict(duration=0),
                                                  fromcurrent=True,
                                                  mode='immediate')]
                            )]
                        ),
                        
                    ]              
                  )
layout.update(xaxis =dict(range=['2022-02-01', '2022-10-31'], autorange=False),
              yaxis =dict(range=[0, 250], autorange=False)); # ajustar o range se precisar colocar os outliers
fig_vendas = go.Figure(data=[trace1], frames=frames, layout=layout)

fig_vendas.show()

C:\Users\ctobr\AppData\Local\Temp\ipykernel_15160\1702761367.py:7: FutureWarning:

The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.

C:\Users\ctobr\AppData\Local\Temp\ipykernel_15160\1702761367.py:8: FutureWarning:

The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.

C:\Users\ctobr\AppData\Local\Temp\ipykernel_15160\1702761367.py:13: FutureWarning:

The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]`

In [62]:
py.plot(fig_vendas, filename='vendas_grafico_animado.html')

'vendas_grafico_animado.html'

# Investigando dados atipicos

In [63]:
# Vendas atípicas no dia 23 de Junho de 2022 entre 16:00 e 17:00

df_invest = pd.DataFrame(transactions).query("data == 'Jun 23, 2022'").groupby(by='hora')['item_count'].sum().reset_index()
df_invest


hora  item_count
0      7           8
1      9           5
2     10           5
3     11           7
4     12           4
5     13           8
6     14           5
7     15           3
8     16        2254
9     17           3
10    18           1

In [64]:
dataframe_to_pdf(df_invest, "investiga.pdf", numpages=(1, 1), pagesize=(11.7, 8.3))

In [65]:
graf = px.line(df_invest, x = 'hora', y = 'item_count', labels= {'item_count':'Itens Vendidos'}, title= 'Itens vendidos no dia 23 de Junho 2022')

py.plot(graf, filename='investiga_graf.html')


'investiga_graf.html'

# Vendas dias de semana (DDS) vs Final de semana (FDS)

In [169]:
dds_vendas= pd.DataFrame(transactions[transactions.tipo_de_dia == 'DDS'].groupby(by='data')['item_count'].sum())
fds_vendas= pd.DataFrame(transactions[transactions.tipo_de_dia == 'FDS'].groupby(by='data')['item_count'].sum())

In [170]:
print('O menor número de vendas em um dia de semana foi: \n{0}'.format(
    dds_vendas.item_count.min()))
print('O número médio de vendas em um dia de semana é: \n{0}'.format(
    dds_vendas.item_count.mean()))
print('O maior número de vendas em um dia de semana foi: \n{0}'.format(
    dds_vendas.item_count.max()))

O menor número de vendas em um dia de semana foi: 
1
O número médio de vendas em um dia de semana é: 
97.02314814814815
O maior número de vendas em um dia de semana foi: 
2303


In [171]:
print('O menor número de vendas em um dia de fim-de-semana foi: \n{0}'.format(
    fds_vendas.item_count.min()))
print('O número médio de vendas em um dia fim-de-semana é: \n{0}'.format(
    fds_vendas.item_count.mean()))
print('O maior número de vendas em um dia fim-de-semana foi: \n{0}'.format(
    fds_vendas.item_count.max()))

O menor número de vendas em um dia de fim-de-semana foi: 
77
O número médio de vendas em um dia fim-de-semana é: 
136.0810810810811
O maior número de vendas em um dia fim-de-semana foi: 
226


In [172]:
single_transaction = pd.DataFrame(transactions.groupby(by='venda')['item_count'].sum())

single_transaction = single_transaction.merge(transactions[['tipo_de_dia','data', 'venda']]\
                                              .drop_duplicates('venda'), left_on=single_transaction.index, 
                                              right_on='venda', how='left', copy=False)

print('O número médio de itens em cada venda por tipo de dia é: \n{0}'.format(
    single_transaction.groupby(by='tipo_de_dia')['item_count'].mean()))

O número médio de itens em cada venda por tipo de dia é: 
tipo_de_dia
DDS    2.780918
FDS    2.836620
Name: item_count, dtype: float64


In [114]:
px.histogram(transactions, x = transactions.groupby(by='data')['item_count'].sum(), histnorm= 'probability density', 
color_discrete_sequence=['green', 'orange'] )

In [144]:
# Histogram of items sold by type of day

trace_dds = go.Histogram(
    x=dds_vendas[dds_vendas.item_count < 200].item_count,
    opacity=0.75,
    name = 'Dia de Semana'
)

trace_fds = go.Histogram(
    x=fds_vendas[fds_vendas.item_count > 1].item_count,
    opacity=0.65,
    name = 'Fim-de-semana',
    nbinsx = 16
)

data = [trace_dds, trace_fds]
layout = go.Layout( title = 'Distribuição das vendas por dias de semana/ finais de semana',
                   xaxis=dict(title='Número de Itens Vendidos'),
                   yaxis=dict(title='Frequencia de vendas'),
                   barmode='overlay'
                   )

fig = go.Figure(data=data, layout=layout)

py.iplot(fig, filename='tipo-de_dia-histograma')

# Faturamento por tipo de dia (DDS x FDS)

In [147]:
dds_fatu= pd.DataFrame(transactions[transactions.tipo_de_dia == 'DDS'].groupby(by='data')['total_item'].sum())
fds_fatu= pd.DataFrame(transactions[transactions.tipo_de_dia == 'FDS'].groupby(by='data')['total_item'].sum())

In [151]:
# Histograma

trace_dds = go.Histogram(
    x=dds_fatu[dds_fatu.total_item  < 8000].total_item,
    opacity=0.75,
    name = 'Dia de Semana'
)

trace_fds = go.Histogram(
    x=fds_fatu[fds_fatu.total_item > 1].total_item,
    opacity=0.65,
    name = 'Fim-de-semana',
    nbinsx = 16
)

data = [trace_dds, trace_fds]
layout = go.Layout( title = 'Distribuição do faturamento por dias de semana/ finais de semana',
                   xaxis=dict(title='Faturamento por dia'),
                   yaxis=dict(title='Frequencia de faturamento diário'),
                   barmode='overlay'
                   )

fig = go.Figure(data=data, layout=layout)

py.iplot(fig, filename='tipo-de_dia-histograma')

# Número de itens vendidos por dia da semana

In [ ]:
# Find the number of itens sold per day of week

agregado_vendas_por_dia = grouped_by_date.merge(transactions[['dia_da_semana', 'horario']], left_index=True, right_on='horario',
                                                        how='left', validate='1:m')

agregado_vendas_por_dia = agregado_vendas_por_dia[~agregado_vendas_por_dia.index.duplicated(keep='first')]

dias = ['segunda-feira','terça-feira','quarta-feira','quinta-feira','sexta-feira','sabado','domingo']

sales_per_day = []

for day in days:
    
    df_days = merged_sales_per_day[merged_sales_per_day.day_of_week == day]
    
    sales_per_day.append(list(df_days['item_count']))

In [165]:
filtro_where = np.where((transactions['dia_da_semana'] =='sábado')& (transactions['hora_do_dia'] == 'manhã'))
transactions.loc[filtro_where]

venda       data     cliente  mesa                         produto  \
353      619 2022-02-05  CONSUMIDOR   M 1                  SOURDOUGH 369G   
354      621 2022-02-05  CONSUMIDOR   M 2      COUVE ABACAXI AGUA DE COCO   
355      621 2022-02-05  CONSUMIDOR   M 2      SANDUICHE DE PEPERONI BRIE   
356      621 2022-02-05  CONSUMIDOR   M 2         CROISSANT MUSSATRELA DE   
357      622 2022-02-05  CONSUMIDOR   M 3           SUCO DE LARANJA 400ML   
358      622 2022-02-05  CONSUMIDOR   M 3        CROISSANT OVOS BACON MEL   
359      623 2022-02-05  CONSUMIDOR   M 2             TORRADA FARINA 165G   
360      623 2022-02-05  CONSUMIDOR   M 2     COUVE LIMAO ABACAXI HORTELA   
361      623 2022-02-05  CONSUMIDOR   M 2      MINI CROISSANT 25G KIT C 5   
362      623 2022-02-05  CONSUMIDOR   M 2     CROISSANT BRIE PARMA MEL DE   
363      624 2022-02-05  CONSUMIDOR   M 4        ABACAXI CURCUMA GENGIBRE   
364      624 2022-02-05  CONSUMIDOR   M 4         CROISSANT MUSSATRELA DE   
365      625 2022-02-05  CONSUMIDOR   M 3     COUVE LIMAO ABACAXI HORTELA   
366      625 2022-02-05  CONSUMIDOR   M 3    CROISANT DE CROISSANT QUEIJO   
367      625 2022-02-05  CONSUMIDOR   M 3     CROISSANT BRIE PARMA MEL DE   
368      628 2022-02-05  CONSUMIDOR   M 2                FOLHADO MACA 80G   
369      628 2022-02-05  CONSUMIDOR   M 2    SOURDOUGH SEMI INTEGRAL 370G   
370      628 2022-02-05  CONSUMIDOR   M 2       TARTELETE DE MORANGO 120G   
371      627 2022-02-05  CONSUMIDOR   M 1       MINI PAIN AU CHOCOLAT 35G   
372      627 2022-02-05  CONSUMIDOR   M 1              PASTEL DE NATA 60G   
373      629 2022-02-05  CONSUMIDOR   M 2      MINI CROISSANT 25G KIT C 5   
374      631 2022-02-05  CONSUMIDOR   M 2         FOCACCIA FORMAGGIO 246G   
375      631 2022-02-05  CONSUMIDOR   M 2    SOURDOUGH AZEITONA E ALECRIM   
376      631 2022-02-05  CONSUMIDOR   M 2      MINI CROISSANT 25G KIT C 5   
377      631 2022-02-05  CONSUMIDOR   M 2         CROISSANT MUSSATRELA DE   
378      633 2022-02-05  CONSUMIDOR   M 2           SUCO DE LARANJA 400ML   
379      633 2022-02-05  CONSUMIDOR   M 2    BOWL DE IOGURTE FRUTAS AVEIA   
380      633 2022-02-05  CONSUMIDOR   M 2        CROISSANT OVOS BACON MEL   
381      633 2022-02-05  CONSUMIDOR   M 2     CROISSANT BRIE PARMA MEL DE   
382      630 2022-02-05  CONSUMIDOR   M 1        FOLHADO MISTO COM TAMARA   
383      630 2022-02-05  CONSUMIDOR   M 1           SUCO DE LARANJA 400ML   
384      632 2022-02-05  CONSUMIDOR   M 3     CROISSANT  TRADICIONAL 80 G   
385      634 2022-02-05  CONSUMIDOR   M 2     CROISSANT BRIE PARMA MEL DE   
386      634 2022-02-05  CONSUMIDOR   M 2     AGUA MINERAL SEM GAS 500 ML   
387      637 2022-02-05  CONSUMIDOR   M 1     BOMBOLONI DOCE DE LEITE 80G   
388      637 2022-02-05  CONSUMIDOR   M 1    SOURDOUGH AZEITONA E ALECRIM   
389      637 2022-02-05  CONSUMIDOR   M 1             TORRADA FARINA 165G   
390      637 2022-02-05  CONSUMIDOR   M 1         CROISSANT MUSSATRELA DE   
391      636 2022-02-05  CONSUMIDOR   M 5           SUCO DE LARANJA 400ML   
392      636 2022-02-05  CONSUMIDOR   M 5              PAO SOURDOUGH OVOS   
393      636 2022-02-05  CONSUMIDOR   M 5      QUICHE DE FRANGO ALHO PORO   
394      636 2022-02-05  CONSUMIDOR   M 5         CROISSANT MUSSATRELA DE   
395      638 2022-02-05  CONSUMIDOR   M 2     BOMBOLONI DOCE DE LEITE 80G   
396      638 2022-02-05  CONSUMIDOR   M 2              PASTEL DE NATA 60G   
397      638 2022-02-05  CONSUMIDOR   M 2              PAO SOURDOUGH OVOS   
398      638 2022-02-05  CONSUMIDOR   M 2     CROISSANT  TRADICIONAL 80 G   
399      638 2022-02-05  CONSUMIDOR   M 2     CROISSANT BRIE PARMA MEL DE   
400      638 2022-02-05  CONSUMIDOR   M 2              SACHE MANTEIGA 10G   
401      638 2022-02-05  CONSUMIDOR   M 2     AGUA MINERAL COM GAS 500 ML   
402      638 2022-02-05  CONSUMIDOR   M 2     AGUA MINERAL SEM GAS 500 ML   
403      639 2022-02-05  CONSUMIDOR   M 1      COUVE ABACAXI AGUA DE COCO   
404

In [161]:
f_filter = transactions['dia_da_semana']=='sábado'
print (transactions[f_filter])

       venda       data     cliente  mesa                         produto  \
353      619 2022-02-05  CONSUMIDOR   M 1                  SOURDOUGH 369G   
354      621 2022-02-05  CONSUMIDOR   M 2      COUVE ABACAXI AGUA DE COCO   
355      621 2022-02-05  CONSUMIDOR   M 2      SANDUICHE DE PEPERONI BRIE   
356      621 2022-02-05  CONSUMIDOR   M 2         CROISSANT MUSSATRELA DE   
357      622 2022-02-05  CONSUMIDOR   M 3           SUCO DE LARANJA 400ML   
358      622 2022-02-05  CONSUMIDOR   M 3        CROISSANT OVOS BACON MEL   
359      623 2022-02-05  CONSUMIDOR   M 2             TORRADA FARINA 165G   
360      623 2022-02-05  CONSUMIDOR   M 2     COUVE LIMAO ABACAXI HORTELA   
361      623 2022-02-05  CONSUMIDOR   M 2      MINI CROISSANT 25G KIT C 5   
362      623 2022-02-05  CONSUMIDOR   M 2     CROISSANT BRIE PARMA MEL DE   
363      624 2022-02-05  CONSUMIDOR   M 4        ABACAXI CURCUMA GENGIBRE   
364      624 2022-02-05  CONSUMIDOR   M 4         CROISSANT MUSSATRELA DE   